In [109]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import NearestNeighbors

In [110]:
data  = pd.read_csv('./dataset/recipes.csv')
data = data.dropna(subset=['CookTime'])
data

RecipeId                                              Name  \
0             38                 Low-Fat Berry Blue Frozen Dessert   
1             39                                           Biryani   
2             40                                     Best Lemonade   
3             41                    Carina's Tofu-Vegetable Kebabs   
4             42                                      Cabbage Soup   
...          ...                                               ...   
522511    541378                         Meg's Pumpkin Spice Bread   
522512    541379                    Meg's Fresh Ginger Gingerbread   
522513    541380  Roast Prime Rib au Poivre with Mixed Peppercorns   
522514    541381                             Kirshwasser Ice Cream   
522516    541383                           Spicy Baked Scotch Eggs   

          AuthorId      AuthorName CookTime PrepTime TotalTime  \
0             1533          Dancer    PT24H    PT45M  PT24H45M   
1             1567        elly9812    PT25M     PT4H   PT4H25M   
2             1566  Stephen Little     PT5M    PT30M     PT35M   
3             1586         Cyclopz    PT20M    PT24H  PT24H20M   
4             1538       Duckie067    PT30M    PT20M     PT50M   
...            ...             ...      ...      ...       ...   
522511  2001302649          Meg J.    PT45M    PT30M   PT1H15M   
522512  2002090414           rdsxc    PT35M     PT1H   PT1H35M   
522513      211566    Denver cooks     PT3H    PT30M   PT3H30M   
522514  2001131545     Jonathan F.     PT3H     PT1H      PT4H   
522516      188099    Chef LauraMD    PT25M    PT15M     PT40M   

               DatePublished  \
0       1999-08-09T21:46:00Z   
1       1999-08-29T13:12:00Z   
2       1999-09-05T19:52:00Z   
3       1999-09-03T14:54:00Z   
4       1999-09-19T06:19:00Z   
...                      ...   
522511  2020-12-22T15:26:00Z   
522512  2020-12-22T15:27:00Z   
522513  2020-12-22T15:32:00Z   
522514  2020-12-22T15:33:00Z   
522516  2020-12-22T22:12:00Z   

                                              Description  \
0       Make and share this Low-Fat Berry Blue Frozen ...   
1       Make and share this Biryani recipe from Food.com.   
2       This is from one of my  first Good House Keepi...   
3       This dish is best prepared a day in advance to...   
4       Make and share this Cabbage Soup recipe from F...   
...                                                   ...   
522511  Even people who claim they don't like pumpkin ...   
522512  Make and share this Meg's Fresh Ginger Gingerb...   
522513  White, black, green, and pink peppercorns add ...   
522514  Make and share this Kirshwasser Ice Cream reci...   
522516  Great way to have hard boiled eggs and crispy,...   

                                                   Images  ...  \
0       c("https://img.sndimg.com/food/image/upload/w_...  ...   
1       c("https://img.sndimg.com/food/image/upload/w_...  ...   
2       c("https://img.sndimg.com/food/image/upload/w_...  ...   
3       c("https://img.sndimg.com/food/image/upload/w_...  ...   
4       "https://img.sndimg.com/food/image/upload/w_55...  ...   
...                                                   ...  ...   
522511  "https://img.sndimg.com/food/image/upload/w_55...  ...   
522512                                       character(0)  ...   
522513  "https://img.sndimg.com/food/image/upload/w_55...  ...   
522514                                       character(0)  ...   
522516                                       character(0)  ...   

       SaturatedFatContent CholesterolContent SodiumContent  \
0                      1.3                8.0          29.8   
1                     16.6              372.8         368.4   
2                      0.0                0.0           1.8   
3                      3.8                0.0        1558.6   
4                      0.1                0.0         959.3   
...                    ...                ...           ...   
522511                

In [111]:
cook_time_list  = [i[2:] for i  in data["CookTime"]]
print(cook_time_list[0])

24H


In [124]:
def categorize_meal(time_list):
    # Check if the total time is less than 30 minutes
    label = []
    for time in time_list: 
        #if it at the hour range, then put it as dinner 
        if "H" in time and "M" in time: 
            print(time, "dinner")
            label.append(2)
        elif time[-1] == "H":
            print(time,"dinner")
            label.append(2)
        elif time[-1] == "M":
            curr_min = time[0:len(time)-1]
            if int(curr_min)  < 20:
                print(curr_min,"breakfast")
                label.append(0) #breakfast
            elif int(curr_min) >= 20 and int(curr_min) < 40:
                print(curr_min,"lunch")
                label.append(1)
            elif int(curr_min) >= 40:
                print(curr_min,"Dinner")
                label.append(2)
    return label

In [125]:
def calc_bmr(weight, height, age, gender):
    #calculate bmr will allow us to further know if the 
    if gender == 0: #if the user is male
        bmr = 10*weight + 6.25*height - 5*age + 5
    else:
        bmr = 10*weight + 6.25*height - 5*age - 161
    return bmr 

In [126]:
def cacl_calories(bmr, exercise_duration):
    #we gonna calculate the needed caloried to be observed per day when 
    #wanting the maintaining weight

    # little to no exercise 
    if exercise_duration == 0:
        calories_per_day  = bmr * 1.2
    # light exercise --> 1 to 3 times per week
    elif exercise_duration == 1:
        calories_per_day  = bmr * 1.35
    elif exercise_duration == 2: #Moderate exercise 
        calories_per_day = bmr * 1.5
    else: #active/intense exercise 
        calories_per_day = bmr * 1.7
    
    return calories_per_day

In [127]:
meal_label = categorize_meal(cook_time_list)
print(len(meal_label))

24H dinner
25 lunch
5 breakfast
20 lunch
30 lunch
2H dinner
3 breakfast
50 Dinner
9 breakfast
30 lunch
50 Dinner
25 lunch
45 Dinner
50 Dinner
2H dinner
1H dinner
2H14M dinner
10 breakfast
42 Dinner
15 breakfast
25 lunch
1H dinner
20 lunch
1H dinner
2H38M dinner
1H50M dinner
3H dinner
43 Dinner
35 lunch
1H dinner
55 Dinner
10 breakfast
3H dinner
45 Dinner
30 lunch
2H37M dinner
2H27M dinner
23 lunch
1H45M dinner
20 lunch
30 lunch
1H dinner
168H dinner
2H dinner
25 lunch
6 breakfast
40 Dinner
1H52M dinner
42 Dinner
1H30M dinner
30 lunch
25 lunch
50 Dinner
40 Dinner
4H15M dinner
55 Dinner
15 breakfast
6H dinner
20 lunch
22 lunch
15 breakfast
1H10M dinner
1H dinner
1H dinner
1H55M dinner
1H5M dinner
20 lunch
10 breakfast
3H dinner
30 lunch
20 lunch
36 lunch
4H dinner
2H dinner
1H5M dinner
3H30M dinner
1H dinner
1H10M dinner
30 lunch
1H6M dinner
8H40M dinner
1H10M dinner
32 lunch
8H dinner
30 lunch
35 lunch
42 Dinner
55 Dinner
2H35M dinner
2H dinner
3H dinner
1H dinner
13H3M dinner
7 breakfa

In [128]:
#add a new column in 
data["Meal Label"] = meal_label

In [129]:
data.head()


RecipeId                               Name  AuthorId      AuthorName  \
0        38  Low-Fat Berry Blue Frozen Dessert      1533          Dancer   
1        39                            Biryani      1567        elly9812   
2        40                      Best Lemonade      1566  Stephen Little   
3        41     Carina's Tofu-Vegetable Kebabs      1586         Cyclopz   
4        42                       Cabbage Soup      1538       Duckie067   

  CookTime PrepTime TotalTime         DatePublished  \
0    PT24H    PT45M  PT24H45M  1999-08-09T21:46:00Z   
1    PT25M     PT4H   PT4H25M  1999-08-29T13:12:00Z   
2     PT5M    PT30M     PT35M  1999-09-05T19:52:00Z   
3    PT20M    PT24H  PT24H20M  1999-09-03T14:54:00Z   
4    PT30M    PT20M     PT50M  1999-09-19T06:19:00Z   

                                         Description  \
0  Make and share this Low-Fat Berry Blue Frozen ...   
1  Make and share this Biryani recipe from Food.com.   
2  This is from one of my  first Good House Keepi...   
3  This dish is best prepared a day in advance to...   
4  Make and share this Cabbage Soup recipe from F...   

                                              Images  ... CholesterolContent  \
0  c("https://img.sndimg.com/food/image/upload/w_...  ...                8.0   
1  c("https://img.sndimg.com/food/image/upload/w_...  ...              372.8   
2  c("https://img.sndimg.com/food/image/upload/w_...  ...                0.0   
3  c("https://img.sndimg.com/food/image/upload/w_...  ...                0.0   
4  "https://img.sndimg.com/food/image/upload/w_55...  ...                0.0   

  SodiumContent CarbohydrateContent FiberContent  SugarContent  \
0          29.8                37.1          3.6          30.2   
1         368.4                84.4          9.0          20.4   
2           1.8                81.5          0.4          77.2   
3        1558.6                64.2         17.3          32.1   
4         959.3                25.1          4.8          17.7   

   ProteinContent  RecipeServings  RecipeYield  \
0             3.2             4.0          NaN   
1            63.4             6.0          NaN   
2             0.3             4.0          NaN   
3            29.3             2.0     4 kebabs   
4             4.3             4.0          NaN   

                                  RecipeInstructions  Meal Label  
0  c("Toss 2 cups berries with sugar.", "Let stan...           2  
1  c("Soak saffron in warm milk for 5 minutes and...           1  
2  c("Into a 1 quart Jar with tight fitting lid, ...           0  
3  c("Drain the tofu, carefully squeezing out exc...           1  
4  c("Mix everything together and bring to a boil...           1  

[5 rows x 29 columns]

In [137]:
# take out each meal period data 
breakfast_data = data[data["Meal Label"]==0]
lunch_data = data[data["Meal Label"]==1]
dinner_data = data[data["Meal Label"]==2]
print(dinner_data)

        RecipeId                                              Name  \
0             38                 Low-Fat Berry Blue Frozen Dessert   
5             43                              Best Blackbottom Pie   
7             45        Buttermilk Pie With Gingersnap Crumb Crust   
12            50                                 Biscotti Di Prato   
15            53                             Jimmy G's Carrot Cake   
...          ...                                               ...   
522505    541372                         Chiles Rellenos Casserole   
522510    541377                   Slow-Cooker Classic Coffee Cake   
522511    541378                         Meg's Pumpkin Spice Bread   
522513    541380  Roast Prime Rib au Poivre with Mixed Peppercorns   
522514    541381                             Kirshwasser Ice Cream   

          AuthorId            AuthorName CookTime PrepTime TotalTime  \
0             1533                Dancer    PT24H    PT45M  PT24H45M   
5            34

In [131]:
#specify the important feature only --> include recipe, nutritions, food name 
important_keys = [0,1,4,16,17,18,19,20,21,22,23,24,27]
breakfast_data = breakfast_data.iloc[:,important_keys]
lunch_data = lunch_data.iloc[:, important_keys]
dinner_data = dinner_data.iloc[:, important_keys]

In [132]:
dinner_data.head()

RecipeId                                        Name CookTime  Calories  \
0         38           Low-Fat Berry Blue Frozen Dessert    PT24H     170.9   
5         43                        Best Blackbottom Pie     PT2H     437.9   
7         45  Buttermilk Pie With Gingersnap Crumb Crust    PT50M     228.0   
12        50                           Biscotti Di Prato    PT50M      89.4   
15        53                       Jimmy G's Carrot Cake    PT45M     372.9   

    FatContent  SaturatedFatContent  CholesterolContent  SodiumContent  \
0          2.5                  1.3                 8.0           29.8   
5         19.3                 10.9                94.3          267.6   
7          7.1                  1.7                24.5          281.8   
12         2.6                  0.3                16.6           23.5   
15        10.6                  3.2                62.0          190.0   

    CarbohydrateContent  FiberContent  SugarContent  ProteinContent  \
0                  37.1           3.6          30.2             3.2   
5                  58.0           1.8          42.5             7.0   
7                  37.5           0.5          24.7             4.2   
12                 14.5           0.8           7.3             2.3   
15                 66.2           3.4          40.9             6.6   

                                   RecipeInstructions  
0   c("Toss 2 cups berries with sugar.", "Let stan...  
5   c("Graham Cracker Crust: In small bowl, combin...  
7   c("Preheat oven to 350°F.", "Make pie crust, u...  
12  c("EGG WASH 1 Egg, large 1 tsp Water In the bo...  
15  c("Grease and lightly flour 2 9x1 1/2-inch rou...

In [133]:
def bmi_cal(weight, height):
    bmi = weight/((height/100)**2) 
    if ( bmi < 16):
        # severly underweight
        return 4
    elif ( bmi >= 16 and bmi < 18.5):
        #underweight
        return 3
    elif ( bmi >= 18.5 and bmi < 25):
        #healthy
        return 2
    elif ( bmi >= 25 and bmi < 30):
        #print overweight
        return 1
    elif ( bmi >=30):
        #obesity
        return 0 

In [134]:
def increase_weight(current_calories, breakfast, lunch, dinner, desire_weight_gain):
    
    calories_per_kilogram = 7700

    # Calculate weekly and daily surplus
    weekly_surplus_calories = desire_weight_gain * calories_per_kilogram
    daily_surplus_calories = weekly_surplus_calories / 7
    target_calorie = current_calories + daily_surplus_calories
    #print(current_calories, target_calorie)
    #distribute the distribution between breakfast, lunch and dinner (20 - 40 - 40)
    breakfast_target_calorie  = target_calorie * 0.2
    lunch_tagret_calorie = target_calorie * 0.35
    dinner_target_calorie = target_calorie * 0.45
    #print(breakfast_target_calorie)
    #selected_columns = 'Calories'
    X_breakfast = breakfast[['Calories']]
    # scaler = StandardScaler()
    # X_scaled = scaler.fit_transform(X)
    # Calculate distances
    distances, indices = NearestNeighbors(n_neighbors=5, metric='euclidean').fit(X_breakfast).kneighbors([[breakfast_target_calorie]])
    # Get the top 5 nearest neighbors
    nearest_neighbors = breakfast_data.iloc[indices[0]]
    print("Top 5 Breakfast Food Choice")
    print(nearest_neighbors[['Name', 'CookTime', 'Calories', 'RecipeInstructions']].reset_index(drop=True))

    X_lunch = lunch[['Calories']]
    distances, indices = NearestNeighbors(n_neighbors=5, metric='euclidean').fit(X_lunch).kneighbors([[lunch_tagret_calorie]])
    # Get the top 5 nearest neighbors
    nearest_neighbors = breakfast_data.iloc[indices[0]]
    print("Top 5 Lunch Food Choice")
    print(nearest_neighbors[['Name', 'CookTime', 'Calories', 'RecipeInstructions']].reset_index(drop=True))


    X_dinner = dinner[['Calories']]
    distances, indices = NearestNeighbors(n_neighbors=5, metric='euclidean').fit(X_dinner).kneighbors([[dinner_target_calorie]])
    # Get the top 5 nearest neighbors
    nearest_neighbors = breakfast_data.iloc[indices[0]]
    print("Top 5 Dinner Food Choice")
    print(nearest_neighbors[['Name', 'CookTime', 'Calories', 'RecipeInstructions']].reset_index(drop=True))



In [143]:
def decrease_weight(current_calories, breakfast, lunch, dinner, desire_weight_decrease):
    
    calories_per_kilogram = 7700

    # Calculate weekly and daily surplus
    weekly_surplus_calories = desire_weight_decrease * calories_per_kilogram
    daily_surplus_calories = weekly_surplus_calories / 7
    target_calorie = current_calories - daily_surplus_calories
    #print(current_calories, target_calorie)
    #distribute the distribution between breakfast, lunch and dinner (20 - 40 - 40)
    breakfast_target_calorie  = target_calorie * 0.2
    lunch_tagret_calorie = target_calorie * 0.35
    dinner_target_calorie = target_calorie * 0.45
    #print(breakfast_target_calorie)
    #selected_columns = 'Calories'
    X_breakfast = breakfast[['Calories']]
    # scaler = StandardScaler()
    # X_scaled = scaler.fit_transform(X)
    # Calculate distances
    distances, indices = NearestNeighbors(n_neighbors=5, metric='euclidean').fit(X_breakfast).kneighbors([[breakfast_target_calorie]])
    # Get the top 5 nearest neighbors
    nearest_neighbors = breakfast_data.iloc[indices[0]]
    print("Top 5 Breakfast Food Choice")
    print(nearest_neighbors[['Name', 'CookTime', 'Calories', 'RecipeInstructions']].reset_index(drop=True))

    X_lunch = lunch[['Calories']]
    distances, indices = NearestNeighbors(n_neighbors=5, metric='euclidean').fit(X_lunch).kneighbors([[lunch_tagret_calorie]])
    # Get the top 5 nearest neighbors
    nearest_neighbors = breakfast_data.iloc[indices[0]]
    print("Top 5 Lunch Food Choice")
    print(nearest_neighbors[['Name', 'CookTime', 'Calories', 'RecipeInstructions']].reset_index(drop=True))


    X_dinner = dinner[['Calories']]
    distances, indices = NearestNeighbors(n_neighbors=5, metric='euclidean').fit(X_dinner).kneighbors([[dinner_target_calorie]])
    # Get the top 5 nearest neighbors
    nearest_neighbors = breakfast_data.iloc[indices[0]]
    print("Top 5 Dinner Food Choice")
    print(nearest_neighbors[['Name', 'CookTime', 'Calories', 'RecipeInstructions']].reset_index(drop=True))



In [144]:
#demo 
user_weight = 65 #in kg
user_height = 165 #in cm
user_age = 25
user_gender = 0 #user gender 
user_exercise_duration = 1 #light exercise 
bmi = bmi_cal(user_weight, user_height) #showing bmi as an additional information for user health
bmr = calc_bmr(user_weight,user_height,user_age,user_gender) #bmr will allow to calculate the calories intake
calories = cacl_calories(bmr, user_exercise_duration)
increase_weight(calories, breakfast_data, lunch_data, dinner_data, 1)

Top 5 Breakfast Food Choice
                                       Name CookTime  Calories  \
0          Delicious Homemade Dijon Mustard     PT6M     641.5   
1  Jimmy Dean's 6-Layer Breakfast Casserole    PT15M     641.5   
2            Barbecued / Grilled Vegetables    PT15M     641.5   
3                             Satay Patties    PT10M     641.5   
4                      Spicy Shepherd's Pie    PT15M     641.5   

                                  RecipeInstructions  
0  c("In a non-stick saucepan combine the wine, o...  
1  c("Preheat oven to 350.", "Place eggs, cream, ...  
2  c("Peel the tough outer casing from the lemon ...  
3  c("Saute onion and garlic in oil until onions ...  
4  c("Preheat the oven to 350 degrees.", "Prepare...  
Top 5 Lunch Food Choice
                                  Name CookTime  Calories  \
0      Roasted Kale With Crumbled Feta    PT15M     299.3   
1                Pork and Fennel Saute    PT15M     276.1   
2   Baked Orzo With Peppers and Cheese

c:\Users\trand\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
c:\Users\trand\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
c:\Users\trand\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(


In [145]:
#demo 
user_weight = 95 #in kg
user_height = 165 #in cm
user_age = 25
user_gender = 0 #user gender 
user_exercise_duration = 1 #light exercise 
bmi = bmi_cal(user_weight, user_height) #showing bmi as an additional information for user health
bmr = calc_bmr(user_weight,user_height,user_age,user_gender) #bmr will allow to calculate the calories intake
calories = cacl_calories(bmr, user_exercise_duration)
decrease_weight(calories, breakfast_data, lunch_data, dinner_data, 1)

Top 5 Breakfast Food Choice
                           Name CookTime  Calories  \
0  Grilled Lemon Garlic Chicken    PT15M     282.5   
1             Beefy Burger Dogs    PT15M     282.5   
2   Low-Fat Baked Cheese Sticks     PT8M     282.5   
3     Pasta and Crab Meat Salad    PT12M     282.5   
4                   Cup Pudding     PT2M     282.5   

                                  RecipeInstructions  
0  c("Mix together all ingredients except chicken...  
1  c("Mix the ground beef with a light dusting of...  
2  c("Set oven to 400 degrees.", "Lightly grease ...  
3  c("Mix Miracle Whip, Italian Dressing, Mayonna...  
4  c("Grease 2 large cups well.", "Sift together ...  
Top 5 Lunch Food Choice
                                                Name CookTime  Calories  \
0                              Cream Cheese Frosting     PT5M     193.1   
1      Fluffy Peanut Butter and Banana Doggie Treats    PT15M      89.3   
2                            Spinach Tortellini Soup    PT15M     29

c:\Users\trand\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
c:\Users\trand\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
c:\Users\trand\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
